## Vector Search 

In [ ]:
import os, pandas as pd
from sqlalchemy import create_engine, text

In [ ]:
username = 'demo'
password = 'demo'
hostname = os.getenv('IRIS_HOSTNAME', 'localhost')
port = '1972' 
namespace = 'USER'
CONNECTION_STRING = f"iris://{username}:{password}@{hostname}:{port}/{namespace}"

engine = create_engine(CONNECTION_STRING)

In [18]:
# Load knowledge graph
entity_embeddings = pd.read_csv('./entity_embeddings.csv', index_col=0)
entity_embeddings["embedding"] = entity_embeddings["embedding"].apply(
    lambda x: x[1:-1])

len_label = entity_embeddings['label'].str.len().max()
len_uri = entity_embeddings['uri'].str.len().max()
# TODO: set varchar length dynamically as above
with engine.connect() as conn:
    with conn.begin(): 
        result = conn.execute(text('DROP TABLE IF EXISTS Test.EntityEmbeddings'))
        sql = f"""
                CREATE TABLE Test.EntityEmbeddings (
                        embedding VECTOR(DOUBLE, 50),
                        label VARCHAR({len_label}),
                        uri VARCHAR({len_uri})
                )
                """
        result = conn.execute(text(sql))

with engine.connect() as conn:
    with conn.begin():
        for index, row in entity_embeddings.iterrows():
            sql = text("""
                INSERT INTO Test.EntityEmbeddings 
                (embedding, label, uri) 
                VALUES (TO_VECTOR(:embedding), :label, :uri)
            """)
            conn.execute(sql, {
                'embedding': str(row['embedding']),
                'label': row['label'], 
                'uri': row['uri']
            })


In [19]:
# Calculate distance between entities
with engine.connect() as conn:
    with conn.begin():
        sql = f"""
                SELECT TOP 10 e1.uri AS uri1, e2.uri AS uri2, e1.label AS label1, e2.label AS label2,
                VECTOR_COSINE(e1.embedding, e2.embedding) AS distance
                FROM Test.EntityEmbeddings e1, Test.EntityEmbeddings e2
                WHERE e1.uri = 'http://identifiers.org/medgen/C0002395'
                ORDER BY distance DESC
                """
        result = conn.execute(text(sql))
        data = result.fetchall()
        display(data)

Exception during reset or similar
Traceback (most recent call last):
  File "/var/folders/g5/qwphv0rn5tvflncj75xsxvxw0000gn/T/ipykernel_77641/1077196279.py", line 11, in <module>
    result = conn.execute(text(sql))
             ^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/aldan.creo/miniconda3/envs/hackupc/lib/python3.11/site-packages/sqlalchemy/engine/base.py", line 1416, in execute
    return meth(
           ^^^^^
  File "/Users/aldan.creo/miniconda3/envs/hackupc/lib/python3.11/site-packages/sqlalchemy/sql/elements.py", line 517, in _execute_on_connection
    return connection._execute_clauseelement(
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/aldan.creo/miniconda3/envs/hackupc/lib/python3.11/site-packages/sqlalchemy/engine/base.py", line 1639, in _execute_clauseelement
    ret = self._execute_context(
          ^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/aldan.creo/miniconda3/envs/hackupc/lib/python3.11/site-packages/sqlalchemy/engine/base.py", line 1848, in _execute_context


ConnectionResetError: [Errno 54] Connection reset by peer

In [ ]:
# Load clinical trials

relation_embeddings = pd.read_csv('./relation_embeddings.csv', index_col=0)
relation_embeddings["embedding"] = relation_embeddings["embedding"].apply(
    lambda x: x[1:-1])

len_label = relation_embeddings['label'].str.len().max()
len_uri = relation_embeddings['uri'].str.len().max()
# TODO: set varchar length dynamically as above
with engine.connect() as conn:
    with conn.begin():# Load 
        result = conn.execute(text('DROP TABLE IF EXISTS Test.RelationEmbeddings'))
        sql = f"""
                CREATE TABLE Test.RelationEmbeddings (
                        embedding VECTOR(DOUBLE, 50),
                        label VARCHAR({len_label}),
                        uri VARCHAR({len_uri})
                )
                """
        result = conn.execute(text(sql))

with engine.connect() as conn:
    with conn.begin():
        for index, row in relation_embeddings.iterrows():
            sql = text("""
                INSERT INTO Test.RelationEmbeddings 
                (embedding, label, uri) 
                VALUES (TO_VECTOR(:embedding), :label, :uri)
            """)
            conn.execute(sql, {
                'embedding': str(row['embedding']),
                'label': row['label'], 
                'uri': row['uri']
            })

In [22]:
# Load knowledge graph
clinical_trials = pd.read_csv("clinical_trials_embeddings.csv")
clinical_trials["embeddings"] = clinical_trials["embeddings"].apply(lambda x: x[1:-1])
display(clinical_trials.head())

# TODO: set varchar length dynamically as above
with engine.connect() as conn:
    with conn.begin():
        result = conn.execute(text("DROP TABLE IF EXISTS Test.ClinicalTrials"))
        sql = f"""
                CREATE TABLE Test.ClinicalTrials (
                        nct_id VARCHAR(11) PRIMARY KEY,
                        diseases TEXT,
                        embedding VECTOR(DOUBLE, 768)
                )
                """
        result = conn.execute(text(sql))

with engine.connect() as conn:
    with conn.begin():
        for index, row in clinical_trials.iterrows():

            sql = text(
                """
                INSERT INTO Test.ClinicalTrials 
                (nct_id, diseases, embedding)
                VALUES (:nct_id, :diseases, TO_VECTOR(:embedding))
            """
            )
            conn.execute(
                sql,
                {
                    "nct_id": row["nct_id"],
                    "diseases": row["desease_condition"],
                    "embedding": str(row["embeddings"]),
                },
            )

desease_condition  \
0  marijuana abuse, substance-related disorders, ...   
1  tuberculosis, latent tuberculosis, infections,...   
2  heart failure, heart diseases, cardiovascular ...   
3  lymphoma, neoplasms by histologic type, neopla...   
4                       anemia, hematologic diseases   

                                          embeddings       nct_id  
0  -0.8323991298675537, 1.47855544090271, 0.00130...  NCT03055377  
1  -0.43443307280540466, 0.9625586271286011, -0.1...  NCT03042754  
2  -0.5791705250740051, 0.13008448481559753, 0.13...  NCT03035123  
3  -0.1608569175004959, 0.8489153981208801, -0.55...  NCT02272751  
4  0.21379394829273224, 0.17073844373226166, -0.1...  NCT00931606

In [21]:
# %%
import pandas as pd
import rdflib

# Load the disease descriptions from MGDEF.RRF
df_disease_descriptions = pd.read_csv("disease_descriptions_with_embeddings.csv")
df_disease_descriptions["embeddings"] = df_disease_descriptions["embeddings"].apply(lambda x: x[1:-1])

with engine.connect() as conn:
    with conn.begin(): 
        result = conn.execute(text('DROP TABLE IF EXISTS Test.DiseaseDescriptions'))
        sql = f"""
                CREATE TABLE Test.DiseaseDescriptions (
                        definition TEXT,
                        uri TEXT,
                        embedding VECTOR(DOUBLE, 768)
                )
                """
        result = conn.execute(text(sql))

with engine.connect() as conn:
    with conn.begin():
        for index, row in df_disease_descriptions.iterrows():
            sql = text("""
                INSERT INTO Test.DiseaseDescriptions 
                (uri, definition, embedding)
                VALUES (:uri, :definition, TO_VECTOR(:embedding))
            """)
            conn.execute(sql, {
                'uri': row['uri'],
                'definition': row['definition'],
                'embedding': str(row['embeddings'])
            })

                                          definition  \
0  A sudden onset of abdominal pain with associat...   
1  A type of abdominal pain characterized by a fe...   
2                         Distention of the abdomen.   
3  An abnormal enlargement or swelling in the abd...   
4      New abnormal growth of tissue in the ABDOMEN.   

                                      uri  \
0  http://identifiers.org/medgen/C0000727   
1  http://identifiers.org/medgen/C0000729   
2  http://identifiers.org/medgen/C0000731   
3  http://identifiers.org/medgen/C0000734   
4  http://identifiers.org/medgen/C0000735   

                                          embeddings  
0  0.07821787893772125, 0.9349365234375, -0.11445...  
1  -0.48267558217048645, 0.8518325090408325, -0.1...  
2  -0.4706612527370453, -0.23200057446956635, -0....  
3  0.03700314462184906, 0.6256464123725891, -0.47...  
4  -0.5286742448806763, 0.06493321806192398, -1.0...  
